### Copy files generated in the TimeSeriesNetworkViz Project (t.get_gexf()) to a workspace in this project

In [1]:
import os
from os.path import join
import shutil
import config as ec

reload_graphs = True

if reload_graphs == True:
    # Remove the files and directories that will be rebuilt
    os.chdir('C:/Users/sgarcia40/UCSC_DBDA_Spring_2020/Project_3/UGraphEmb/data/Project/train')
    !rm *.gexf
    
    os.chdir('C:/Users/sgarcia40/UCSC_DBDA_Spring_2020/Project_3/UGraphEmb/data/Project/test')
    !rm *.gexf
    
    os.chdir('C:/Users/sgarcia40/UCSC_DBDA_Spring_2020/Project_3/UGraphEmb/save/ds_mat')
    !rm -rf project*.pickle

    os.chdir('C:/Users/sgarcia40/UCSC_DBDA_Spring_2020/Project_3/UGraphEmb/save/ProjectData')
    !rm -rf *.klepto

    os.chdir('C:/Users/sgarcia40/UCSC_DBDA_Spring_2020/Project_3/UGraphEmb/save/SiameseModelData')
    !rm -rf None_project*.klepto

    os.chdir('C:/Users/sgarcia40/UCSC_DBDA_Spring_2020/Project_3/UGraphEmb/save')
    !rm -rf project*.pickle

    # Copy files from final_gexf_graphs to data/Project/train
    src1 = 'C:/Users/sgarcia40/ML Projects/Causal Inference/kdd2018-tutorial/TimeSeriesNetworkViz/final_gexf_graphs'
    dest1 = 'C:/Users/sgarcia40/UCSC_DBDA_Spring_2020/Project_3/UGraphEmb/data/Project/train'

    i = 0
    src_files = os.listdir(src1)
    for file_name in src_files:
        full_file_name = os.path.join(src1, file_name)
        if os.path.isfile(full_file_name):
            shutil.copy(full_file_name, dest1)
            i+=1
        
    print("The number of graphs copied to ~/data/Project/train is: ", i)
    
    # move some files from the training folder to the test folder
    src2 = 'C:/Users/sgarcia40/UCSC_DBDA_Spring_2020/Project_3/UGraphEmb/data/Project/train'
    dest2 = 'C:/Users/sgarcia40/UCSC_DBDA_Spring_2020/Project_3/UGraphEmb/data/Project/test'

    ttl_cnt_train_initial = i
    num_files_to_move = int(ttl_cnt_train_initial * ec.valid_percentage)
    num_files_in_train = ttl_cnt_train_initial - num_files_to_move
    
    j = ttl_cnt_train_initial - 1
    k = 0
    src_files = os.listdir(src2)
    for file_name in src_files:
        if k == num_files_to_move:
            break
        
        file_name = (str(j) + ".gexf")
        full_file_name = os.path.join(src2, file_name)
        if os.path.isfile(full_file_name):
            shutil.move(full_file_name, dest2)
            j-=1
            k+=1
            
    print("folder counts: train initial: ", ttl_cnt_train_initial, ", Post file move: Train: ", num_files_in_train, ", Test: ", num_files_to_move)   
    


In [2]:
#!/usr/bin/python3
from __future__ import division
from __future__ import print_function
from __future__ import absolute_import

import os
from os.path import join
import shutil
import numpy as np
import pandas as pd
from time import time
import enum
import tensorflow as tf
from collections import OrderedDict, defaultdict
import networkx as nx

import config as ec
from utils_siamese import extract_config_code, convert_long_time_to_str, convert_msec_to_sec_str, get_coarsen_level
from data_siamese import SiameseModelData
from model import Model
from samplers import SelfShuffleList
from inits import glorot
from saver import Saver
from dist_sim_calculator import DistSimCalculator, get_gs_ds_mat
from dist_sim_kernel import create_ds_kernel
from glob import glob
from sklearn.manifold import TSNE
from utils import load, save, create_dir_if_not_exists, get_save_path, load_data, get_data_path
from shapely.geometry import Point, LineString
from data import load_glabels_from_txt
%load_ext tensorboard

- Entered data::Data Class
- Entered data::SynData Class
- Entered data::IMDBMultiData Class
- Entered data::NCI109Data Class
- Entered data::WebEasyData Class
- Entered data::Reddit5kData Class
- Entered data::Reddit10kData Class
- Entered data::Reddit10kSmallData Class
- Entered data::PTCData Class
- Entered data::ProjectData Class
- Entered utils::exec_turnon_print Global Method
- Entered data_siamese::SiameseModelData Class
- Entered data_siamese::ModelGraph Class
- Entered data_siamese::NodeFeatureEncoder Class
- Entered data_siamese::NodeFeatureOneHotEncoder Class
- Entered data_siamese::NodeFeatureConstantEncoder Class
- Entered data_siamese::GraphLabelOneHotEncoder Class
- Entered layers::Layer Class
- Entered layers::Dense Class
- Entered layers::GraphConvolution Class
- Entered layers::GraphConvolutionAttention Class
- Entered layers::Coarsening Class
- Entered layers::Average Class
- Entered layers::Attention Class
- Entered layers::GMNAverage Class
- Entered layers::Jumping

In [3]:
# Let's disable all the warnings first
import warnings
warnings.simplefilter("ignore")

# obtain current time
t = time()

# turn off eager execution
tf.compat.v1.disable_eager_execution()

logging_enabled = True

os.environ["CUDA_VISIBLE_DEVICES"] = str(ec.gpu)
config = tf.compat.v1.ConfigProto()
config.gpu_options.allow_growth = True

In [4]:
data = SiameseModelData(ec.dataset_train)

- Entered data_siamese::SiameseModelData::__init__ Constructor Method
- Entered data_siamese::SiameseModelData::get_name Public Method
- Entered data::Data::__init__ Constructor Method
- Entered data::Data::name_suffix Public Method
- Entered data::Data::save_filename Public Method
- Entered utils::get_save_path Global Method
- Entered utils::get_root_path Global Method
- Entered utils::load Global Method
- Entered utils::proc_filepath Global Method
- Entered utils::append_ext_to_filepath Global Method
- Entered utils::load_klepto Global Method
info: SiameseModelData\None_project_gcn_onehot_type_bfs_None_False_0.2
Data config obtained from C:\Users\sgarcia40\UCSC_DBDA_Spring_2020\Project_3\UGraphEmb\save\SiameseModelData\None_project_gcn_onehot_type_bfs_None_False_0.2

237 train graphs; 60 validation graphs; 74 test graphs


In [5]:
# load the graph labels from file and transform into an array of glabels
filepath = '{}\\{}\\glabels.txt'.format(get_data_path(), 'Project')
glabels_dic = load_glabels_from_txt(filepath)        

glabel_data = list(glabels_dic.items())
tmp_arr_2d = np.array(glabel_data)

_, glabels = zip(*tmp_arr_2d) 
glabels = np.asarray(glabels)

- Entered utils::get_data_path Global Method
- Entered utils::get_root_path Global Method
- Entered data::load_glabels_from_txt Global Method
- Entered utils::append_ext_to_filepath Global Method


In [6]:
# Clear logs from previous runs

# cwd = os.getcwd()
# print("info: The current working directory is: ", cwd)

!rm -rf logs/siamese*

rm: cannot remove 'logs/siamese_regression_project/test_info.klepto/K_graph_embs_mat': Device or resource busy


### Create the SiameseRegressionModel Class 

In [7]:
def create_model(model, input_dim, data, dist_sim_calculator):
    if logging_enabled == True:
        print("- Entered ugraphemb::create_model Global Method")

    if model in ['siamese_regression']:
        return SiameseRegressionModel(input_dim, data, dist_sim_calculator)
    else:
        raise RuntimeError('Unknown model {}'.format(model))

class SiameseRegressionModel(Model):
    if logging_enabled == True:
        print("- Entered ugraphemb::SiameseRegressionModel Class")

    def __init__(self, input_dim, data, dist_sim_calculator):
        if logging_enabled == True:
            print("- Entered ugraphemb::SiameseRegressionModel::__init__ Constructor Method")

        self.input_dim = input_dim
        print('info: original_input_dim', self.input_dim)
        
        # for the project,
        # - ec.batch_size = 2, i.e., Number of graph pairs in a batch
        # - level = 1, i.e., coursening is not used
        self._create_basic_placeholders(ec.batch_size, ec.batch_size, level=get_coarsen_level())
        
        self.train_y_true = tf.compat.v1.placeholder(tf.float32, shape=(ec.batch_size, 1))
        self.val_test_y_true = tf.compat.v1.placeholder(tf.float32, shape=(1, 1))
        
        # Build the model.
        super(SiameseRegressionModel, self).__init__()
        
        # for the project,
        # - ec.ds_kernel = exp
        # - ec.yeta = None
        # - ec.scale = 0.7, i.e., Scale for the exp/inverse kernel function
        self.ds_kernel = create_ds_kernel(ec.ds_kernel, ec.yeta, ec.scale)        
        self.train_triples = self._load_train_triples(data, dist_sim_calculator)

    def pred_sim_without_act(self):
        if logging_enabled == True:
            print("- Entered ugraphemb::SiameseRegressionModel::pred_sim_without_act Public Method")
        
        return self.val_test_pred_score

    def apply_final_act_np(self, score):
        if logging_enabled == True:
            print("- Entered apply_final_act_np Public Method")
        
        return score

    def get_feed_dict_for_train(self, data):
        if logging_enabled == True:
            print("- Entered ugraphemb::SiameseRegressionModel::get_feed_dict_for_train Public Method")
        
        rtn = {}
        pairs = []
        y_true = np.zeros((ec.batch_size, 1))
        glabels = None
        
        for i in range(ec.batch_size):
            g1, g2, true_sim_dist = self._sample_train_pair(data)
            pairs.append((g1, g2))
            y_true[i] = true_sim_dist
            # print("pairs: ", pairs, ", true_sim_dist: ", true_sim_dist)
        
        rtn[self.train_y_true] = y_true
        rtn[self.dropout] = ec.dropout_rate
        
        return self._supply_laplacians_etc_to_feed_dict(rtn, pairs, 'train')

    def get_feed_dict_for_val_test(self, g1, g2, true_sim_dist):
        if logging_enabled == True:
            print("- Entered ugraphemb::SiameseRegressionModel::get_feed_dict_for_val_test Public Method")
        
        rtn = {}
        pairs = [(g1, g2)]
        y_true = np.zeros((1, 1))
        y_true[0] = true_sim_dist
        rtn[self.val_test_y_true] = y_true
        
        return self._supply_laplacians_etc_to_feed_dict(rtn, pairs, 'val_test')

    def get_true_dist_sim(self, i, j, true_result):
        if logging_enabled == True:
            print("- Entered ugraphemb::SiameseRegressionModel::get_true_dist_sim Public Method")
        
        assert (true_result.dist_or_sim() in ['sim', 'dist'])  # A* GED or MCS
        _, ds = true_result.dist_sim(i, j, ec.ds_norm)
        
        if ec.supply_sim_dist == 'sim' and true_result.dist_or_sim() == 'dist':  # e.g. A*
            assert (ec.ds_metric == 'ged')
            rtn = self.ds_kernel.dist_to_sim_np(ds)
        elif ec.supply_sim_dist == 'dist' and true_result.dist_or_sim() == 'sim':  # e.g. MCS
            assert (ec.ds_metric == 'mcs')
            raise NotImplementedError()  # TODO
        else:
            rtn = ds
        
        return rtn

    def _get_ins(self, layer, tvt):
        if logging_enabled == True:
            print("- Entered ugraphemb::SiameseRegressionModel::_get_ins Private Method")
        
        ins = []
        assert (layer.__class__.__name__ == 'GraphConvolution' or
                layer.__class__.__name__ == 'GraphConvolutionAttention')
            
        for features in (self._get_plhdr('features_1', tvt) +
                         self._get_plhdr('features_2', tvt)):
            
            ins.append(features)
        
        return ins

    def _proc_ins_for_merging_layer(self, ins, _):
        if logging_enabled == True:
            print("- Entered ugraphemb::SiameseRegressionModel::_proc_ins_for_merging_layer Private Method")
        
        assert (len(ins) % 2 == 0)
        proc_ins = []
        i = 0
        j = len(ins) // 2
        
        for _ in range(len(ins) // 2):
            proc_ins.append([ins[i], ins[j]])
            i += 1
            j += 1
        
        return proc_ins

    def _val_test_pred_score(self):
        if logging_enabled == True:
            print("- Entered ugraphemb::SiameseRegressionModel::_val_test_pred_score Private Method")
        
        self.val_test_output = self._stack_concat(self.val_test_output)
        assert self.val_test_output.get_shape().as_list() == [1, 1], self.val_test_output.get_shape()
        
        return tf.squeeze(self.val_test_output)

    def _task_loss(self, tvt):
        if logging_enabled == True:
            print("- Entered ugraphemb::SiameseRegressionModel::_task_loss Private Method")
        
        # Using enum class create enumerations
        class loss_type(enum.Enum):
            lambda_msel = 1
            lambda_wdl = 2
            lambda_tsl = 3
            lambda_del = 4

        rtn = {}
        for loss_lambda in loss_type:        
            print("loss_lambda: ", loss_lambda)

            if (loss_lambda == loss_type.lambda_msel) and (ec.lambda_mse_loss > 0):
                print("loss_lambda: ", loss_lambda)
                # If the model predicts sim, ground-truth should be sim.
                # If the model predicts dist, ground-truth should be dist.
                assert (ec.supply_sim_dist == ec.pred_sim_dist)
                y_pred, y_true = self._get_y_pred_y_true(tvt)
                loss = tf.nn.l2_loss(y_true - y_pred)
                rtn['mse_loss'] = ec.lambda_mse_loss * loss
            
            # elif (loss_lambda == "loss_type.lambda_wdl") and (ec.lambda_weighted_dist_loss > 0):
            elif (loss_lambda == loss_type.lambda_wdl) and (ec.lambda_weighted_dist_loss > 0):
                print("loss_lambda: ", loss_lambda)
                # The model must predict dist and ground-truth must be sim.
                assert (ec.pred_sim_dist == 'dist')
                assert (ec.supply_sim_dist == 'sim')
                assert (ec.ds_metric == 'ged')
                y_pred, y_true_sim = self._get_y_pred_y_true(tvt)
                assert (y_true_sim.get_shape() == y_pred.get_shape())
                loss = tf.reduce_mean(y_true_sim * y_pred)
                rtn['weighted_dist_loss'] = ec.lambda_weighted_dist_loss * loss
            
            elif (loss_lambda == loss_type.lambda_tsl) and (ec.lambda_triv_avoid_loss > 0):
                print("loss_lambda: ", loss_lambda)
                phi, bs_times_2, D = self._get_graph_embs_as_one_mat(tvt)
                loss = tf.reduce_mean(phi ** 2)  # tf.nn.l2_loss does not do sqrt
                rtn['triv_avoid_loss'] = ec.lambda_triv_avoid_loss * loss
            
            elif (loss_lambda == loss_type.lambda_del) and (ec.lambda_diversity_loss > 0):
                print("loss_lambda: ", loss_lambda)
                phi, bs_times_2, D = self._get_graph_embs_as_one_mat(tvt)
                # phi /= bs_times_2
                phi_T_phi = tf.matmul(tf.transpose(phi), phi)
                should = tf.eye(D)
                assert (phi_T_phi.get_shape() == should.get_shape())
                loss = tf.reduce_mean((phi_T_phi - should) ** 2)  # tf.nn.l2_loss does not do sqrt
                rtn['diversity_loss'] = ec.lambda_diversity_loss * loss
            
            elif loss_lambda == 'lambda_gc_loss':
                print("loss_lambda == lambda_gc_loss")
                pass  # handled by model
        
        return rtn

    def _get_y_pred_y_true(self, tvt):
        if logging_enabled == True:
            print("- Entered ugraphemb::SiameseRegressionModel::_get_y_pred_y_true Private Method")
        if tvt == 'train':
            y_pred = self._stack_concat(self.train_outputs)
            y_true = self.train_y_true            
        else:
            y_pred = self._stack_concat(self.val_test_output)
            y_true = self.val_test_y_true
        
        assert (y_true.get_shape() == y_pred.get_shape())
        
        return y_pred, y_true

    def _get_graph_embs_as_one_mat(self, tvt):
        if logging_enabled == True:
            print("- Entered ugraphemb::SiameseRegressionModel::_get_graph_embs_as_one_mat Private Method")
        
        phi = self._get_graph_embds(tvt, True)
        s = phi.get_shape().as_list()
        bs_times_2, D = s[0], s[1]
        bs = ec.batch_size if tvt == 'train' else 1
        
        assert (bs_times_2 == bs * 2)
        
        return phi, bs_times_2, D

    def _get_graph_embds(self, tvt, need_concat):
        if logging_enabled == True:
            print("- Entered ugraphemb::SiameseRegressionModel::_get_graph_embds Private Method")
        
        if tvt == 'train':
            rtn = self.graph_embeddings_train
        else:
            assert (tvt == 'val')
            rtn = self.graph_embeddings_val_test
        
        if need_concat:
            return self._stack_concat(rtn)
        else:
            return rtn

    def _create_basic_placeholders(self, num1, num2, level):
        if logging_enabled == True:
            print("- Entered ugraphemb::SiameseRegressionModel::_create_basic_placeholders Private Method")
        
        self.laplacians_1 = [[[tf.compat.v1.sparse_placeholder(tf.float32)]
              for _ in range(level)] for _ in range(num1)]
        
        self.laplacians_2 = [[[tf.compat.v1.sparse_placeholder(tf.float32)]
              for _ in range(level)] for _ in range(num2)]
        
        self.features_1 = [tf.compat.v1.sparse_placeholder(tf.float32) for _ in range(num1)]        
        self.features_2 = [tf.compat.v1.sparse_placeholder(tf.float32) for _ in range(num2)]        
        self.num_nonzero_1 = [tf.compat.v1.placeholder(tf.int32) for _ in range(num1)]        
        self.num_nonzero_2 = [tf.compat.v1.placeholder(tf.int32) for _ in range(num2)]
        self.edge_index_1 = [tf.compat.v1.sparse_placeholder(tf.int32, shape=(None, 2)) for _ in range(num1)]
        self.edge_index_2 = [tf.compat.v1.sparse_placeholder(tf.int32, shape=(None, 2)) for _ in range(num2)]
        self.incidence_mat_1 = [tf.compat.v1.sparse_placeholder(tf.int32) for _ in range(num1)]
        self.incidence_mat_2 = [tf.compat.v1.sparse_placeholder(tf.int32) for _ in range(num2)]
        self.dropout = tf.compat.v1.placeholder_with_default(0., shape=())
        self.val_test_laplacians_1 = [[[tf.compat.v1.sparse_placeholder(tf.float32)] for _ in range(level)]]
        self.val_test_laplacians_2 = [[[tf.compat.v1.sparse_placeholder(tf.float32)] for _ in range(level)]]
        self.val_test_features_1 = [tf.compat.v1.sparse_placeholder(tf.float32)]
        self.val_test_features_2 = [tf.compat.v1.sparse_placeholder(tf.float32)]
        self.val_test_num_nonzero_1 = [tf.compat.v1.placeholder(tf.int32)]
        self.val_test_num_nonzero_2 = [tf.compat.v1.placeholder(tf.int32)]
        self.val_test_edge_index_1 = [tf.compat.v1.sparse_placeholder(tf.int32, shape=(None, 2))]
        self.val_test_edge_index_2 = [tf.compat.v1.sparse_placeholder(tf.int32, shape=(None, 2))]
        self.val_test_incidence_mat_1 = [tf.compat.v1.sparse_placeholder(tf.int32)]
        self.val_test_incidence_mat_2 = [tf.compat.v1.sparse_placeholder(tf.int32)]

    def _load_train_triples(self, data, ds_calc):
        if logging_enabled == True:
            print("- Entered ugraphemb::SiameseRegressionModel::_load_train_triples Private Method")
        
        triples = []
        triples = self._load_real_pairs(data.train_gs, data.train_gs, 'train', 'train', triples, ds_calc)
        print("triples: ", triples)
                
        return SelfShuffleList(triples)

    def _load_real_pairs(self, gs1, gs2, tvt1, tvt2, triples, ds_calc):
        if logging_enabled == True:
            print("- Entered ugraphemb::SiameseRegressionModel::_load_real_pairs Private Method")
        
        rtn = []
        nx_gs1 = self._get_nxgraph_list(gs1)
        nx_gs2 = self._get_nxgraph_list(gs2)

        ds_mat = get_gs_ds_mat(
            nx_gs1, nx_gs2, ds_calc, tvt1, tvt2,
            ec.dataset_train, ec.ds_metric, ec.ds_algo, ec.ds_norm,
            dec_gsize=ec.supersource, return_neg1=True)
        
        m, n = ds_mat.shape
        # assert (m == n)
        # ds_mat_idx = np.argsort(ds_mat, axis=1)
        valid_count, skip_count = 0, 0
        
        for i in range(m):
            g1 = gs1[i]
            
            for j in range(n):
                col = j
                g2, ds = gs2[col], ds_mat[i][col]
                
                if ds < 0:
                    skip_count += 1
                    if tvt1 == 'test':
                        print('@@@', i, j, g1.nxgraph.graph['gid'], g2.nxgraph.graph['gid'],
                              len(gs1), len(gs2))
                        exit()
                    continue
                valid_count += 1
                
                if ec.ds_metric == 'mcs' or ec.ds_metric == 'glet':
                    assert (ec.supply_sim_dist == 'sim')  # TODO: transform mcs to dist if needed
                    need = ds
                else:
                    assert (ec.ds_metric == 'ged')
                    if ec.supply_sim_dist == 'sim':  # supply for train --> consistent with supply_sim_dist
                        # for exp kernal: np.exp(-self.scale * ds)
                        need = self.ds_kernel.dist_to_sim_np(ds)
                    else:
                        need = ds
                
                rtn.append((g1, g2, need))
        
        if ec.train_real_percent < 1:
            sp = int(len(rtn) * ec.train_real_percent)
            rtn_new = rtn[0:sp]
            print('info: Only take {} from {} due to {} percent'.format(
                len(rtn_new), len(rtn), ec.train_real_percent))
            rtn = rtn_new
        
        triples += rtn
        
        print('info: {} valid pairs; {} pairs with dist or sim < 0; {} total triples'.format(
            valid_count, skip_count, len(triples)))
        
        return triples

    def _sample_train_pair(self, data):
        if logging_enabled == True:
            print("- Entered ugraphemb::SiameseRegressionModel::_sample_train_pair Private Method")
        
        x, y, true_sim_dist = self.train_triples.get_next()
        
        return x, y, true_sim_dist

    def _supply_laplacians_etc_to_feed_dict(self, feed_dict, pairs, tvt):
        if logging_enabled == True:
            print("- Entered ugraphemb::SiameseRegressionModel::_supply_laplacians_etc_to_feed_dict Private Method")
        
        for i, (g1, g2) in enumerate(pairs):
            feed_dict[self._get_plhdr('features_1', tvt)[i]] = g1.get_node_inputs()
            feed_dict[self._get_plhdr('features_2', tvt)[i]] = g2.get_node_inputs()
            feed_dict[self._get_plhdr('num_nonzero_1', tvt)[i]] = g1.get_node_inputs_num_nonzero()
            feed_dict[self._get_plhdr('num_nonzero_2', tvt)[i]] = g2.get_node_inputs_num_nonzero()
            feed_dict[self._get_plhdr('edge_index_1', tvt)[i]] = g1.edge_index
            feed_dict[self._get_plhdr('edge_index_2', tvt)[i]] = g2.edge_index
            feed_dict[self._get_plhdr('incidence_mat_1', tvt)[i]] = g1.incidence_mat
            feed_dict[self._get_plhdr('incidence_mat_2', tvt)[i]] = g2.incidence_mat
            assert g1.incidence_mat is not None

            num_laplacians = 1

            for j in range(get_coarsen_level()):
                for k in range(num_laplacians):
                    feed_dict[self._get_plhdr('laplacians_1', tvt)[i][j][k]] = g1.get_laplacians(j)[k]
                    feed_dict[self._get_plhdr('laplacians_2', tvt)[i][j][k]] = g2.get_laplacians(j)[k]
        
        return feed_dict

    def _get_loss_lambdas_flags(self):
        if logging_enabled == True:
            print("- Entered ugraphemb::SiameseRegressionModel::_get_loss_lambdas_flags Private Method")
        
        rtn = []
        d = flag_values_dict()
        
        for k in d.keys():
            if 'lambda_' in k:
                flag_split = k.split('_')
                assert (flag_split[0] == 'lambda')
                assert (flag_split[-1] == 'loss')
                rtn.append(k)
        
        return rtn

    def _get_nxgraph_list(self, model_graphs):
        if logging_enabled == True:
            print("- Entered ugraphemb::SiameseRegressionModel::_get_nxgraph_list Private Method")
        
        return [g.nxgraph for g in model_graphs]


- Entered ugraphemb::SiameseRegressionModel Class


In [8]:
# when running the TF Project:
# - ec_dataset_train is set to 'project'
# - ec.ds_metric is set to 'ged', i.e., distance
# - ec.ds_algo is set to 'astar', i.e., shortest distance

dist_sim_calculator = DistSimCalculator(ec.dataset_train, ec.ds_metric, ec.ds_algo)

- Entered dist_sim_calculator::DistSimCalculator::__init__ Constructor Method
- Entered utils::get_save_path Global Method
- Entered utils::get_root_path Global Method
- Entered utils::load Global Method
- Entered utils::proc_filepath Global Method
- Entered utils::append_ext_to_filepath Global Method
- Entered utils::load_pkl Global Method
info: Loaded dist/sim map from C:\Users\sgarcia40\UCSC_DBDA_Spring_2020\Project_3\UGraphEmb\save\project_ged_astar_gidpair_dist_map with 56169 entries


In [9]:
# Note, if gidpair_ds_map needs to be rebuilt, make sure to delete both of the following files,
# - UGraphEmb\save\project_ged_astar_gidpair_dist_map.pickle
# - UGraphEmb\save\ds_mat\project_train(206)_train(206)_ds_mat_ged_norm_astar.pickle
# Otherwise, gidpair_ds_map will not get built.

# %%pixie_debugger

# when running the TF Project:
# - ec.model is set to 'siamese_regression'
# - data.input_dim(), see info: print statement below
model = create_model(ec.model, data.input_dim(), data, dist_sim_calculator)

- Entered data_siamese::SiameseModelData::input_dim Public Method
- Entered data_siamese::NodeFeatureOneHotEncoder::input_dim Public Method
- Entered ugraphemb::create_model Global Method
- Entered ugraphemb::SiameseRegressionModel::__init__ Constructor Method
info: original_input_dim 248
- Entered ugraphemb::SiameseRegressionModel::_create_basic_placeholders Private Method
- Entered model::Model::__init__ Constructor Method
- Entered model::Model::_build Private Method
- Entered layers_factory::create_layers Global Method
- Entered layers_factory::create_GraphConvolution_layer Global Method
- Entered layers_factory::parse_as_bool Global Method
- Entered layers_factory::parse_as_bool Global Method
- Entered layers_factory::create_activation Global Method
- Entered layers_factory::parse_as_bool Global Method
- Entered layers::GraphConvolution::__init__ Constructor Method
- Entered layers::Layer::__init__ Constructor Method
- Entered layers::get_layer_name Global Method
- Entered layers:

- Entered layers::GraphConvolution::_call_one_graph Private Method
- Entered layers::GraphConvolution::_gcn Private Method
- Entered layers::sparse_dropout Global Method
- Entered layers::GraphConvolution::_call_one_graph Private Method
- Entered layers::GraphConvolution::_gcn Private Method
- Entered layers::sparse_dropout Global Method
- Entered model::Model::_proc_outs Private Method
- Entered model::Model::_stack_concat Private Method
- Entered model::Model::_log_mat Private Method
	 2_graphconvolution_2
- Entered model::Model::_proc_ins Private Method
- Entered model::Model::_supply_laplacians_etc_to_ins Private Method
- Entered model::Model::_get_plhdr Private Method
- Entered model::Model::_get_plhdr Private Method
- Entered model::Model::_get_plhdr Private Method
- Entered model::Model::_get_plhdr Private Method
- Entered model::Model::_get_plhdr Private Method
- Entered model::Model::_get_plhdr Private Method
- Entered model::Model::_get_plhdr Private Method
- Entered model::M

- Entered layers::Attention::_gen_att Private Method
- Entered layers::interact_two_sets_of_vectors Global Method
- Entered layers::Attention::_call_one_mat Private Method
- Entered layers::Attention::_gen_att Private Method
- Entered layers::interact_two_sets_of_vectors Global Method
- Entered layers::Attention::_call_one_mat Private Method
- Entered layers::Attention::_gen_att Private Method
- Entered layers::interact_two_sets_of_vectors Global Method
- Entered layers::Attention::_call_one_mat Private Method
- Entered layers::Attention::_gen_att Private Method
- Entered layers::interact_two_sets_of_vectors Global Method
- Entered layers::Layer::__call__ Private Method
- Entered layers::Average::_call Private Method
- Entered layers::Attention::_call_one_mat Private Method
- Entered layers::Attention::_gen_att Private Method
- Entered layers::interact_two_sets_of_vectors Global Method
- Entered layers::Attention::_call_one_mat Private Method
- Entered layers::Attention::_gen_att Priva

ins[i]:  SparseTensor(indices=Tensor("Placeholder_56:0", shape=(None, None), dtype=int64), values=Tensor("Placeholder_55:0", shape=(None,), dtype=float32), dense_shape=Tensor("Placeholder_54:0", shape=(None,), dtype=int64)) , laplacians[gcn_id]:  [<tensorflow.python.framework.sparse_tensor.SparseTensor object at 0x000001B77A098108>] , num_nonzero:  Tensor("Placeholder_60:0", dtype=int32) , edge_index:  SparseTensor(indices=Tensor("Placeholder_63:0", shape=(None, 2), dtype=int64), values=Tensor("Placeholder_62:0", shape=(None,), dtype=int32), dense_shape=Tensor("PlaceholderWithDefault_5:0", shape=(2,), dtype=int64)) , incidence_mat:  SparseTensor(indices=Tensor("Placeholder_68:0", shape=(None, None), dtype=int64), values=Tensor("Placeholder_67:0", shape=(None,), dtype=int32), dense_shape=Tensor("Placeholder_66:0", shape=(None,), dtype=int64))
ins[i]:  SparseTensor(indices=Tensor("Placeholder_59:0", shape=(None, None), dtype=int64), values=Tensor("Placeholder_58:0", shape=(None,), dtype=

- Entered layers::Attention::_gen_att Private Method
- Entered layers::interact_two_sets_of_vectors Global Method
- Entered layers::Attention::_call_one_mat Private Method
- Entered layers::Attention::_gen_att Private Method
- Entered layers::interact_two_sets_of_vectors Global Method
- Entered model::Model::_proc_outs Private Method
- Entered model::Model::_stack_concat Private Method
- Entered layers::Layer::produce_node_atts Public Method
	 8_dense_1
- Entered model::Model::_proc_ins Private Method
- Entered model::Model::_stack_concat Private Method
- Entered layers::Layer::merge_graph_level_embs Public Method
- Entered model::Model::_has_seen_merge_layer Private Method
- Entered layers::Layer::merge_graph_level_embs Public Method
- Entered layers::Layer::merge_graph_level_embs Public Method
- Entered layers::Layer::merge_graph_level_embs Public Method
- Entered layers::Average::merge_graph_level_embs Private Method
- Entered layers::Layer::__call__ Private Method
- Entered layers:

...

- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public

- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public

- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public

- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public Method
- Entered dist_sim_kernel::GaussianKernel::dist_to_sim_np Public

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [10]:
sess = tf.compat.v1.Session(config=config)
sess.run(tf.compat.v1.global_variables_initializer())

In [11]:
saver = Saver(sess)
conf_code = extract_config_code()
saver.save_conf_code(conf_code)

- Entered saver::Saver::__init__ Constructor Method
- Entered saver::Saver::_get_model_str Private Method
- Entered utils::create_dir_if_not_exists Global Method
- Entered saver::Saver::_extract_loss_related_summaries_as_list Private Method
Logging to C:\Users\sgarcia40\UCSC_DBDA_Spring_2020\Project_3\UGraphEmb\model\Siamese\logs\siamese_regression_project
- Entered saver::Saver::save_conf_code Public Method


### Training Section

#### Training Method Definitions

In [26]:
def train_loop(data, model, saver, sess):
    if logging_enabled == True:
        print("- Entered ugraphemb::train_loop Global Method")

    # initialize vars...
    train_costs, train_times, ss, val_results_dict = [], [], [], OrderedDict()
    print('* Optimization Started!')
    
    # iters = epochs
    for iter in range(ec.iters):
        iter += 1
        tvt = get_train_tvt(iter)
        
        # Train.
        feed_dict = model.get_feed_dict_for_train(data)
        r, train_time = run_tf(feed_dict, model, saver, sess, tvt, iter=iter)
        train_s = ''
        train_cost = r
        train_costs.append(train_cost)
        train_times.append(train_time)
        
        s = '\tIter:{:04n} {} train_loss={:.5f}{} time={}'.format(
            iter, tvt, train_cost, train_s, convert_msec_to_sec_str(train_time))
        
        print(s)
        ss.append(s)
    
    print('* Optimization Finished!')
    
    return train_costs, train_times


def run_pairs_for_val_test(row_graphs, col_graphs, eval, model, saver,
                           sess, val_or_test, care_about_loss=False):
    if logging_enabled == True:
        print("- Entered ugraphemb::run_pairs_for_val_test Global Method")
    
    m = len(row_graphs)
    n = len(col_graphs)
    sim_dist_mat = np.zeros((m, n))
    time_list = []
    loss_list = []
    print_count = 0
    flush = True
    
    for i in range(m):
        for j in range(n):
            g1 = row_graphs[i]
            g2 = col_graphs[j]
    
            if care_about_loss:
                # true_sim_dist = eval.get_true_dist_sim(i, j, val_or_test, model)
                true_sim_dist = eval(get_true_dist_sim(i, j, val_or_test, model))
                if true_sim_dist is None:
                    continue
            else:
                true_sim_dist = 0  # only used for loss
            # feed_dict = model.get_feed_dict_for_val_test(g1, g2, true_sim_dist, False)
            feed_dict = model.get_feed_dict_for_val_test(g1, g2, true_sim_dist)
            # (loss_i_j, dist_sim_i_j), test_time = run_tf(feed_dict, model, saver, sess, val_or_test)
            # (loss_i_j, dist_sim_i_j), test_time = run_tf(feed_dict, model, saver, sess, val_or_test, iter=iter)
            r, test_time = run_tf(feed_dict, model, saver, sess, val_or_test, iter=iter)
            
            if flush:
                # (loss_i_j, dist_sim_i_j), test_time = run_tf(feed_dict, model, saver, sess, val_or_test)
                r, test_time = run_tf(feed_dict, model, saver, sess, val_or_test, iter=iter)
                flush = False
            
            test_time *= 1000
            
            print("r: ", r)
            if val_or_test == 'test' and print_count < 100000:
                print('{},{},{:.2f}mec,{:.4f}'.format(
                    i, j, test_time, r))
                print_count += 1
            
            # sim_dist_mat[i][j] = dist_sim_i_j
            # loss_list.append(loss_i_j)
            loss_list.append(r)
            time_list.append(test_time)
    
    return loss_list, time_list

def run_tf(feed_dict, model, saver, sess, tvt, iter=None):
    if logging_enabled == True:
        print("- Entered ugraphemb::run_tf Global Method") 
        
    if tvt == 'train':
        objs = [model.opt_op, model.train_loss]
    
    elif tvt == 'test':
        objs = [model.pred_sim_without_act()]
        print("tvt == test objs: ", objs)
    
    elif tvt == 'test_node_emb':
        objs = [model.node_embeddings]
    
    elif tvt == 'test_graph_emb':
        objs = [model.graph_embeddings_val_test]
    
    else:
        raise RuntimeError('Unknown train_test {}'.format(tvt))
    
    objs = saver.proc_objs(objs, tvt, iter)  # may become [loss_related_obj, objs...]
    t = time()
    outs = sess.run(objs, feed_dict=feed_dict)
    time_rtn = time() - t
    saver.proc_outs(outs, tvt, iter)
    
    if tvt == 'train':
        rtn = outs[-1]
    else:
        rtn = outs[-1]
    return rtn, time_rtn

def collect_embeddings(test_gs, train_gs, model, saver, sess, gemb_only=False):
    if logging_enabled == True:
        print("- Entered ugraphemb::collect_embeddings Global Method")
    
    assert (hasattr(model, 'node_embeddings'))
    all_gs = train_gs + test_gs
    node_embs_dict = defaultdict(list)  # {0: [], 1: [], ...}
    graph_embs_mat, emb_time = None, None
    
    if hasattr(model, 'graph_embeddings_val_test'):
        graph_embs_mat = np.zeros((len(all_gs), model.gemb_dim))
    emb_time_list = []
    
    for i, g in enumerate(all_gs):
        feed_dict = model.get_feed_dict_for_val_test(g, g, 1.0)
        
        if not gemb_only:
            node_embs, t = run_tf(
                feed_dict, model, saver, sess, 'test_node_emb')
            t *= 1000
            emb_time_list.append(t)
        
            for gcn_id, node_embs_list_length_two in enumerate(node_embs):
                assert (len(node_embs_list_length_two) == 2)
                node_embs_dict[gcn_id].append(node_embs_list_length_two[0])
        
        # Only collect graph-level embeddings when the model produces them.
        if hasattr(model, 'graph_embeddings_val_test'):
            graph_embs, _ = run_tf(
                feed_dict, model, saver, sess, 'test_graph_emb')
            
            assert (len(graph_embs) == 2)
            graph_embs_mat[i] = graph_embs[0]
    
    if emb_time_list:
        emb_time = np.mean(emb_time_list)
        print('info: node embedding time {:.5f}msec'.format(emb_time))
    
    if hasattr(model, 'graph_embeddings_val_test') and not gemb_only:
        print('info: ', graph_embs_mat[0:2])
    
    return node_embs_dict, graph_embs_mat, emb_time

def get_train_tvt(iter):
    if logging_enabled == True:
        print("- Entered ugraphemb::get_train_tvt Global Method")
    
    tf_opt = 'train'
    
    return tf_opt

def pretty_print_dict(d, indent=0):
    if logging_enabled == True:
        print("- Entered ugraphemb::pretty_print_dict Global Method")
    
    for key, value in sorted(d.items()):
        print('\t' * indent + str(key))
        
        if isinstance(value, dict):
            pretty_print_dict(value, indent + 1)
        else:
            print('\t' * (indent + 1) + str(value))

#### Train the Model

In [13]:
train_costs, train_times = train_loop(data, model, saver, sess)

- Entered ugraphemb::train_loop Global Method
* Optimization Started!
- Entered ugraphemb::get_train_tvt Global Method
- Entered ugraphemb::SiameseRegressionModel::get_feed_dict_for_train Public Method
- Entered ugraphemb::SiameseRegressionModel::_sample_train_pair Private Method
- Entered ugraphemb::SiameseRegressionModel::_sample_train_pair Private Method
- Entered ugraphemb::SiameseRegressionModel::_supply_laplacians_etc_to_feed_dict Private Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs_num_nonzero Public Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs_num_nonzero Public Method
- Entered data_siamese::ModelGraph::get_

- Entered data_siamese::ModelGraph::get_node_inputs_num_nonzero Public Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered model::Model::_get_plhdr Private Method
- Entered model::Model::_get_plhdr Private Method
- Entered model::Model::_get_plhdr Private Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_laplacians Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_laplacians Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs_num_nonzero Public Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method


- Entered saver::Saver::proc_outs Public Method
	Iter:0020 train train_loss=46.73420 time=16.00msec
- Entered ugraphemb::get_train_tvt Global Method
- Entered ugraphemb::SiameseRegressionModel::get_feed_dict_for_train Public Method
- Entered ugraphemb::SiameseRegressionModel::_sample_train_pair Private Method
- Entered ugraphemb::SiameseRegressionModel::_sample_train_pair Private Method
- Entered ugraphemb::SiameseRegressionModel::_supply_laplacians_etc_to_feed_dict Private Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs_num_nonzero Public Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs_num_nonzero Public Method
- Entered 

- Entered saver::Saver::proc_outs Public Method
	Iter:0029 train train_loss=40.18204 time=15.01msec
- Entered ugraphemb::get_train_tvt Global Method
- Entered ugraphemb::SiameseRegressionModel::get_feed_dict_for_train Public Method
- Entered ugraphemb::SiameseRegressionModel::_sample_train_pair Private Method
- Entered ugraphemb::SiameseRegressionModel::_sample_train_pair Private Method
- Entered ugraphemb::SiameseRegressionModel::_supply_laplacians_etc_to_feed_dict Private Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs_num_nonzero Public Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs_num_nonzero Public Method
- Entered 

- Entered saver::Saver::proc_outs Public Method
	Iter:0038 train train_loss=34.55019 time=17.97msec
- Entered ugraphemb::get_train_tvt Global Method
- Entered ugraphemb::SiameseRegressionModel::get_feed_dict_for_train Public Method
- Entered ugraphemb::SiameseRegressionModel::_sample_train_pair Private Method
- Entered ugraphemb::SiameseRegressionModel::_sample_train_pair Private Method
- Entered ugraphemb::SiameseRegressionModel::_supply_laplacians_etc_to_feed_dict Private Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs_num_nonzero Public Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs_num_nonzero Public Method
- Entered 

...

- Entered saver::Saver::proc_outs Public Method
	Iter:0455 train train_loss=2.81163 time=17.00msec
- Entered ugraphemb::get_train_tvt Global Method
- Entered ugraphemb::SiameseRegressionModel::get_feed_dict_for_train Public Method
- Entered ugraphemb::SiameseRegressionModel::_sample_train_pair Private Method
- Entered ugraphemb::SiameseRegressionModel::_sample_train_pair Private Method
- Entered ugraphemb::SiameseRegressionModel::_supply_laplacians_etc_to_feed_dict Private Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs_num_nonzero Public Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs_num_nonzero Public Method
- Entered d

- Entered saver::Saver::proc_outs Public Method
	Iter:0465 train train_loss=2.71625 time=14.01msec
- Entered ugraphemb::get_train_tvt Global Method
- Entered ugraphemb::SiameseRegressionModel::get_feed_dict_for_train Public Method
- Entered ugraphemb::SiameseRegressionModel::_sample_train_pair Private Method
- Entered ugraphemb::SiameseRegressionModel::_sample_train_pair Private Method
- Entered ugraphemb::SiameseRegressionModel::_supply_laplacians_etc_to_feed_dict Private Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs_num_nonzero Public Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs_num_nonzero Public Method
- Entered d

- Entered saver::Saver::proc_outs Public Method
	Iter:0474 train train_loss=2.60358 time=16.00msec
- Entered ugraphemb::get_train_tvt Global Method
- Entered ugraphemb::SiameseRegressionModel::get_feed_dict_for_train Public Method
- Entered ugraphemb::SiameseRegressionModel::_sample_train_pair Private Method
- Entered ugraphemb::SiameseRegressionModel::_sample_train_pair Private Method
- Entered ugraphemb::SiameseRegressionModel::_supply_laplacians_etc_to_feed_dict Private Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs_num_nonzero Public Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs_num_nonzero Public Method
- Entered d

- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs_num_nonzero Public Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs_num_nonzero Public Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered model::Model::_get_plhdr Private Method
- Entered model::Model::_get_plhdr Private Method
- Entered model::Model::_get_plhdr Private Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_laplacians Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_

- Entered data_siamese::ModelGraph::get_laplacians Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_laplacians Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs_num_nonzero Public Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs_num_nonzero Public Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered model::Model::_get_plhdr Private Method
- Entered model::Model::_get_plhdr Private Method
- Entered model::Model::_get_plhdr Private Method


### Testing Section

#### Testing Method Definitions

In [33]:
def test(data, model, saver, sess):
    if logging_enabled == True:
        print("- Entered ugraphemb::test Global Method")
    
    gs1, gs2 = data.test_gs, data.train_gs + data.val_gs
    node_embs_dict, graph_embs_mat, emb_time = collect_embeddings(gs1, gs2, model, saver, sess)
    
    val_or_test = 'test'
    loss_list, time_list = run_pairs_for_val_test(gs1, gs2, eval, model, saver, 
                                                                sess, val_or_test, care_about_loss=False)
    
    print("loss_list:\n", loss_list)
    
    saver.save_test_info(node_embs_dict, graph_embs_mat, emb_time)
    
    return loss_list, time_list

#### Test the Model

In [ ]:
loss_list, time_list = test(data, model, saver, sess)

- Entered ugraphemb::test Global Method
- Entered ugraphemb::collect_embeddings Global Method
- Entered ugraphemb::SiameseRegressionModel::get_feed_dict_for_val_test Public Method
- Entered ugraphemb::SiameseRegressionModel::_supply_laplacians_etc_to_feed_dict Private Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs_num_nonzero Public Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs_num_nonzero Public Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered model::Model::_get_plhdr Private Method
- Entered model::Model::_get_plhdr Private Method
- En

- Entered saver::Saver::proc_outs Public Method
- Entered ugraphemb::SiameseRegressionModel::get_feed_dict_for_val_test Public Method
- Entered ugraphemb::SiameseRegressionModel::_supply_laplacians_etc_to_feed_dict Private Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs_num_nonzero Public Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs_num_nonzero Public Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered model::Model::_get_plhdr Private Method
- Entered model::Model::_get_plhdr Private Method
- Entered model::Model::_get_plhdr Private Method


- Entered saver::Saver::proc_outs Public Method
- Entered ugraphemb::run_tf Global Method
- Entered saver::Saver::proc_objs Public Method
- Entered saver::Saver::proc_outs Public Method
- Entered ugraphemb::SiameseRegressionModel::get_feed_dict_for_val_test Public Method
- Entered ugraphemb::SiameseRegressionModel::_supply_laplacians_etc_to_feed_dict Private Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs_num_nonzero Public Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs_num_nonzero Public Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered mo

- Entered saver::Saver::proc_outs Public Method
- Entered ugraphemb::SiameseRegressionModel::get_feed_dict_for_val_test Public Method
- Entered ugraphemb::SiameseRegressionModel::_supply_laplacians_etc_to_feed_dict Private Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs_num_nonzero Public Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs_num_nonzero Public Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered model::Model::_get_plhdr Private Method
- Entered model::Model::_get_plhdr Private Method
- Entered model::Model::_get_plhdr Private Method


- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_laplacians Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered ugraphemb::run_tf Global Method
- Entered saver::Saver::proc_objs Public Method
- Entered saver::Saver::proc_outs Public Method
- Entered ugraphemb::run_tf Global Method
- Entered saver::Saver::proc_objs Public Method
- Entered saver::Saver::proc_outs Public Method
- Entered ugraphemb::SiameseRegressionModel::get_feed_dict_for_val_test Public Method
- Entered ugraphemb::SiameseRegressionModel::_supply_laplacians_etc_to_feed_dict Private Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs_num_nonzero Public Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
-

...

- Entered ugraphemb::run_tf Global Method
- Entered ugraphemb::SiameseRegressionModel::pred_sim_without_act Public Method
tvt == test objs:  [<tf.Tensor 'Squeeze:0' shape=() dtype=float32>]
- Entered saver::Saver::proc_objs Public Method
- Entered saver::Saver::proc_outs Public Method
r:  0.93684286
1,88,16.01mec,0.9368
- Entered ugraphemb::SiameseRegressionModel::get_feed_dict_for_val_test Public Method
- Entered ugraphemb::SiameseRegressionModel::_supply_laplacians_etc_to_feed_dict Private Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs_num_nonzero Public Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs_num_nonzero Public

- Entered data_siamese::ModelGraph::get_laplacians Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered ugraphemb::run_tf Global Method
- Entered ugraphemb::SiameseRegressionModel::pred_sim_without_act Public Method
tvt == test objs:  [<tf.Tensor 'Squeeze:0' shape=() dtype=float32>]
- Entered saver::Saver::proc_objs Public Method
- Entered saver::Saver::proc_outs Public Method
r:  0.9367697
1,95,20.99mec,0.9368
- Entered ugraphemb::SiameseRegressionModel::get_feed_dict_for_val_test Public Method
- Entered ugraphemb::SiameseRegressionModel::_supply_laplacians_etc_to_feed_dict Private Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs_num_nonzero Public Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Ente

tvt == test objs:  [<tf.Tensor 'Squeeze:0' shape=() dtype=float32>]
- Entered saver::Saver::proc_objs Public Method
- Entered saver::Saver::proc_outs Public Method
r:  0.93678635
1,102,22.14mec,0.9368
- Entered ugraphemb::SiameseRegressionModel::get_feed_dict_for_val_test Public Method
- Entered ugraphemb::SiameseRegressionModel::_supply_laplacians_etc_to_feed_dict Private Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs_num_nonzero Public Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs_num_nonzero Public Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Meth

- Entered ugraphemb::SiameseRegressionModel::_supply_laplacians_etc_to_feed_dict Private Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs_num_nonzero Public Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs_num_nonzero Public Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered model::Model::_get_plhdr Private Method
- Entered model::Model::_get_plhdr Private Method
- Entered model::Model::_get_plhdr Private Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_laplacians Public Method
- Entered model::Mo

- Entered saver::Saver::proc_outs Public Method
r:  0.94783145
1,117,23.25mec,0.9478
- Entered ugraphemb::SiameseRegressionModel::get_feed_dict_for_val_test Public Method
- Entered ugraphemb::SiameseRegressionModel::_supply_laplacians_etc_to_feed_dict Private Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs_num_nonzero Public Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered data_siamese::ModelGraph::get_node_inputs_num_nonzero Public Method
- Entered data_siamese::ModelGraph::get_node_inputs Public Method
- Entered model::Model::_get_plhdr Private Method
- Entered model::Model::_get_plhdr Private Method
- Entered model::Model::_get_plhdr Private Method
- Entered mod

In [30]:
overall_time = convert_long_time_to_str(time() - t)

print("Total Time: ", overall_time, "\nModeling Data: ", saver.get_log_dir(), "\n")
saver.save_overall_time(overall_time)

# print("info: train_costs:\n", train_costs, "\n")
# print("info: train_times:\n", train_times)

- Entered saver::Saver::get_log_dir Public Method
Total Time:  0 days 0 hours 21 mins 28.3 secs 
Modeling Data:  C:\Users\sgarcia40\UCSC_DBDA_Spring_2020\Project_3\UGraphEmb\model\Siamese\logs\siamese_regression_project 

- Entered saver::Saver::save_overall_time Public Method
- Entered saver::Saver::_save_to_result_file Private Method


In [31]:
import matplotlib
import matplotlib.pyplot as plt
import seaborn as sns
sns.set()
# %matplotlib inline

num_points = 6

class LineInterp(object):
    if logging_enabled == True:
        print("- Entered ugraphemb::LineInterp Class")
    
    def __init__(self, x1, y1, x2, y2, num_points):
        if logging_enabled == True:
            print("- Entered ugraphemb::LineInterp::__init__ Constructor Method")
        
        assert (num_points >= 2)
        self.x1, self.y1, self.x2, self.y2, self.num_points = x1, y1, x2, y2, num_points

    def name(self):
        if logging_enabled == True:
            print("- Entered ugraphemb::LineInterp::name Public Method")
        
        return 'line_interp_x1={}_y1={}_x2={}_y2={}_{}ps'.format(self.x1, self.y1, self.x2, self.y2, self.num_points)

# confs = [LineInterp(x1=12, y1=-18, x2=30, y2=10, num_points=12)]
# confs = [LineInterp(x1=50, y1=-45, x2=120, y2=25, num_points=num_points)]
confs = [LineInterp(x1=-20, y1=-40, x2=20, y2=40, num_points=num_points)]
# confs = [LineInterp(x1=-100, y1=-100, x2=100, y2=100, num_points=num_points)]

DATASET = 'project'
DIR = 'C:\\Users\\sgarcia40\\UCSC_DBDA_Spring_2020\\Project_3\\UGraphEmb\\model\\Siamese\\logs\\siamese_regression_project'

# DATASET = 'webeasy'
# DIR = 'C:\\Users\\sgarcia40\\UCSC_DBDA_Spring_2020\\Project_3\\UGraphEmb\\model\\Siamese\\logs\\siamese_regression_webeasy'

# DATASET = 'imdbmulti'
# DIR = 'C:\\Users\\sgarcia40\\UCSC_DBDA_Spring_2020\\Project_3\\UGraphEmb\\model\\Siamese\\logs\\siamese_regression_imdbmulti'

# DATASET = 'reddit10k'
# DIR = 'C:\\Users\\sgarcia40\\UCSC_DBDA_Spring_2020\\Project_3\\UGraphEmb\\model\\Siamese\\logs\\siamese_regression_reddit10k'

# DATASET = 'ptc'
# DIR = 'C:\\Users\\sgarcia40\\UCSC_DBDA_Spring_2020\\Project_3\\UGraphEmb\\model\\Siamese\\logs\\siamese_regression_ptc'

# DATASET = 'nci109'
# DIR = 'C:\\Users\\sgarcia40\\UCSC_DBDA_Spring_2020\\Project_3\\UGraphEmb\\model\\Siamese\\logs\\siamese_regression_nci109'

- Entered ugraphemb::LineInterp Class
- Entered ugraphemb::LineInterp::__init__ Constructor Method


In [ ]:
with plt.xkcd():
    plt.plot(train_costs, label='train')
    plt.title('Loss vs Epochs')
    plt.xlabel('Epochs')
    plt.ylabel('Training Loss')
    plt.grid(True)
    
plt.show()

In [32]:
with plt.xkcd():
    plt.plot(loss_list, label='test')
    plt.title('Loss vs Epochs')
    plt.xlabel('Epochs')
    plt.ylabel('Testing Loss')
    plt.grid(True)
    
plt.show()

NameError: name 'loss_list' is not defined

In [ ]:

def load_embs():
    if logging_enabled == True:
        print("- Entered ugraphemb::load_embs Global Method")
    
    klepto_pickle_dir = join(DIR, 'test_info.klepto')
    tsned_path = join(klepto_pickle_dir, 'tsne_2')
    l = load(klepto_pickle_dir)
    
    if not l:
        raise RuntimeError('Not loaded')
    if 'graph_embs_mat' in l:
        orig_embs = l['graph_embs_mat']  # siamese
    elif 'P' in l:
        orig_embs = l['P']  # kernel
    else:
        assert (False)
    
    print('loaded {}'.format(orig_embs.shape))
    tsne = TSNE(n_components=2)
    embs = tsne.fit_transform(orig_embs)
    
    print('TSNE embeddings: {} --> {} to plot'.format(
        orig_embs.shape, embs.shape))
    save(tsned_path, embs)
    print('Saved to', tsned_path)
    
    return embs

def to_points(embs):
    if logging_enabled == True:
        print("- Entered ugraphemb::to_points Global Method")
    
    assert (embs.shape[1] == 2)
    
    rtn = []
    for emb in embs:
        rtn.append(Point(emb))
    
    print('Created {} Point objects'.format(len(rtn)))
    
    return rtn

def plot_conf(points, conf):
    if logging_enabled == True:
        print("- Entered ugraphemb::plot_conf Global Method")
    
    gs = load_data(DATASET, True).graphs + load_data(DATASET, False).graphs
    line = LineString([(conf.x1, conf.y1), (conf.x2, conf.y2)])
    print(line)
    selected_ps = []
    selected_gs = []
    
    for perc in get_percs(conf):
        lp = line.interpolate(perc, normalized=True)
        id, emb_p = closest_point(lp, points)
        selected_gs.append(gs[id])
        selected_ps.append(emb_p)
    
    print('plotting...')
            
    plot_points(points, [], conf, False)
    plot_points(points, [], conf, True)
    plot_points(points, selected_ps, conf, True)
    plot_gs(selected_gs, conf)

def plot_points(points, selected_ps, conf, include_non_impacting):
    if logging_enabled == True:
        print("- Entered ugraphemb::plot_points Global Method")
    
    # for binary case
    # colors = np.array(["lightcoral", "teal"])

    # for multi-class case
    group = np.array(['Non-Impacting', 
              'AR_AS_MAD_Single_Intf_or_Node',
              'Distribution_Router', 
              'Core_Router_Single_Intf_or_Node', 
              'Core_Router_Multiple_Intf_or_Node', 
              'Border_Router_Single_Intf_or_Node', 
              'Border_Router_Multiple_Intf_or_Node', 
              'L3TV_H5_Controller_or_Nodes'])

    cdict = {'Non-Impacting': 'chartreuse', 
             'AR_AS_MAD_Single_Intf_or_Node': 'yellow', 
             'Distribution_Router': 'darkgreen',
             'Core_Router_Single_Intf_or_Node': 'red', 
             'Core_Router_Multiple_Intf_or_Node': 'magenta',
             'Border_Router_Single_Intf_or_Node': 'orange', 
             'Border_Router_Multiple_Intf_or_Node': 'blue',
             'L3TV_H5_Controller_or_Nodes': 'darkred'
            }

    dx1 = []
    dy1 = []
    glabel_list = []
    group_list = []

    # for p in points:
    for i, p in enumerate(points):
        dx1.append(get_coord(p)[0])
        dy1.append(get_coord(p)[1])
        glabel_list.append(glabels[i])
        group_list.append(group[glabels[i]])
    
    d1 = list(zip(dx1, dy1, glabel_list, group_list))
    d1 = pd.DataFrame(d1, columns=('x', 'y', 'glabel', 'group'))
    
    if include_non_impacting == False:
        d1 = d1.drop(d1[(d1.glabel==0) | (d1.glabel==1)].index)

    plt.figure(figsize=(12, 12))        
    
    x = np.array(d1['x'])
    y = np.array(d1['y'])

    for i, g in enumerate(np.unique(d1['group'])):
        ix = np.where(d1['group'] == g)
        plt.scatter(x[ix], y[ix], c=cdict[g], label=g, s=125, alpha=0.6, edgecolors='black')
      
    dx2 = []
    dy2 = []        
    if selected_ps:
        # for p in selected points:
        for i, p in enumerate(selected_ps):
            dx2.append(get_coord(p)[0])
            dy2.append(get_coord(p)[1])

        d2 = list(zip(dx2, dy2))
        d2 = pd.DataFrame(d2, columns=('x', 'y'))

        x = np.array(d2['x'])
        y = np.array(d2['y'])

        plt.scatter(x, y, facecolors='none', edgecolors='red', s=300)    
        for i in range(len(selected_ps)):
            plt.annotate(i+1, xy=(d2["x"].iloc[i]+0.25, d2["y"].iloc[i]+0.25), fontsize=15, color='black')
        
    if not selected_ps:
        plt.grid(linestyle='dashed')
        name = '{}_grid_tsne'.format(DATASET)
    
    else:
        # plt.axis('off')
        plt.grid(linestyle='dashed')
        cur_axes = plt.gca()
        cur_axes.axes.get_xaxis().set_visible(True)
        cur_axes.axes.get_yaxis().set_visible(True)
        name = '{}_{}_tsne'.format(DATASET, conf.name())

    # for binary case
    # plt.legend(['Non-Impacting', 'Impacting'])
    
    # for multi-class case
    
    plt.legend()

    plt.tight_layout()
    plt.show()

def plot_gs(selected_gs, conf):
    if logging_enabled == True:
        print("- Entered ugraphemb::plot_gs Global Method")

    nrows = int(num_points / 3)
    print("nrows: ", nrows)
    fig, axes = plt.subplots(nrows=nrows, ncols=3, figsize=(20, 20))
    ax = axes.flatten()

    for i in range(len(selected_gs)):
        nx.draw_networkx(
            selected_gs[i], 
            pos=nx.spring_layout(selected_gs[i]),
            ax=ax[i],
            font_size=14,
            font_color='black')
                
        #ax[i].set_axis_off()

    plt.show()
        
def closest_point(lp, points):
    # if logging_enabled == True:
    #     print("- Entered ugraphemb::closest_point Global Method")

    dists = []
    
    for point in points:
        dists.append(lp.distance(point))

    id = np.argmin(dists)
    return id, points[id]

def get_percs(conf):
    if logging_enabled == True:
        print("- Entered ugraphemb::get_percs Global Method")
    
    return list(np.arange(0, 1, 1 / (conf.num_points - 1))) + [1]

def get_coord(point):
    # if logging_enabled == True:
    #     print("- Entered ugraphemb::get_coord Global Method")
    
    return list(point.coords)[0]

In [ ]:
embs = load_embs()

In [ ]:
points = to_points(embs)

In [ ]:
for conf in confs:
    print("conf: ", conf.name())
    plot_conf(points, conf)

In [ ]:
# .tensorboarde_info directory can be found at:
#   C:\Users\sgarcia40\AppData\Local\Temp

# %tensorboard --help
# %tensorboard --inspect --logdir="C:/Users/sgarcia40/UCSC_DBDA_Spring_2020/Project_3/UGraphEmb/model/Siamese/logs/siamese_regression_project/train"

# %tensorboard --logdir=C:/Users/sgarcia40/UCSC_DBDA_Spring_2020/Project_3/UGraphEmb/model/Siamese/logs/siamese_regression_project/train

In [ ]:
# for e in tf.compat.v1.train.summary_iterator("C:/Users/sgarcia40/UCSC_DBDA_Spring_2020/Project_3/UGraphEmb/model/Siamese/logs/siamese_regression_project/train/events.out.tfevents.1592697621.WASNOLP0701209"):
#     for v in e.summary.value:
#         print(v)